## PyTorch train model

### Wczytanie niezbędnych bibliotek

In [289]:
import pandas as pd
import torch
from torch import nn
from sklearn.preprocessing import LabelEncoder

### Wczytanie danych z pliku

In [290]:
data = pd.read_csv('../data/btc_test.csv')
data = pd.DataFrame(data)

### Przygotowanie danych
Powinienembył zrobić to w zadaniu 1

In [291]:
le = LabelEncoder()
data['date'] = le.fit_transform(data['date'])
data['hour'] = le.fit_transform(data['hour'])
data['Volume BTC'] = data['Volume BTC']/10

# Przekształć łańcuchy znaków na liczby aby zapobiec 'TypeError: can't convert np.ndarray of type numpy.object_.'
for col in data.columns:
    data[col] = pd.to_numeric(data[col], errors='coerce')

# Zamień brakujące wartości na 0 aby zapobiec 'IndexError: Target -9223372036854775808 is out of bounds.'
data = data.fillna(0)

### Przygotowanie inputs oraz targets

In [292]:
# Przekształć dane na tensory PyTorch
inputs = torch.tensor(data[['date', 'hour', 'Volume BTC']].values, dtype=torch.float32)

### Model

In [293]:
model = nn.Sequential(
    nn.Flatten(),
    nn.Linear(inputs.shape[1], 64),
    nn.ReLU(),
    nn.Linear(64, 1),
)

### Wczytanie wytrenowanego modelu

In [294]:
model.load_state_dict(torch.load("model.pth"))
model.eval()

Sequential(
  (0): Flatten(start_dim=1, end_dim=-1)
  (1): Linear(in_features=3, out_features=64, bias=True)
  (2): ReLU()
  (3): Linear(in_features=64, out_features=1, bias=True)
)

### Predykcja modelu

In [298]:
predictions = model(inputs)
predicted_data = (predictions.float() * 10)
print(predicted_data)

tensor([[772837.5000],
        [772837.5000],
        [772837.5000],
        ...,
        [772837.5000],
        [772837.5000],
        [772837.5000]], grad_fn=<MulBackward0>)


### Zapis danych do pliku csv

In [300]:
predicted_data_df = pd.DataFrame(torch.detach(predicted_data).numpy())
predicted_data_df.to_csv("predict_result.csv", index=False)

TypeError: detach() missing 1 required positional arguments: "input"